In [1]:
!pip install -q pyomo
!pip install -q folium
!apt update
!apt install -y -q coinor-cbc
!apt install -y -q glpk-utils

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.7/10.7 MB 52.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.6/49.6 kB 4.0 MB/s eta 0:00:00
Get:1 https://cloud.r-project.org/bin/linux/ubuntu focal-cran40/ InRelease [3,622 B]
Hit:2 http://archive.ubuntu.com/ubuntu focal InRelease
Hit:3 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2004/x86_64  InRelease
Get:4 http://security.ubuntu.com/ubuntu focal-security InRelease [114 kB]
Get:5 http://archive.ubuntu.com/ubuntu focal-updates InRelease [114 kB]
Get:6 http://archive.ubuntu.com/ubuntu focal-backports InRelease [108 kB]
Hit:7 http://ppa.launchpad.net/c2d4u.team/c2d4u4.0+/ubuntu focal InRelease
Get:8 https://cloud.r-project.org/bin/linux/ubuntu focal-cran40/ Packages [77.6 kB]
Hit:9 http://ppa.launchpad.net/cran/libgit2/ubuntu focal InRelease
Get:10 http://archive.ubuntu.com/ubuntu focal-updates/universe amd64 Packages [1,334 kB]
Hit:11 http://ppa.launchpad.net/deadsnakes/ppa/ubuntu focal InRelease
Ge

In [2]:
import numpy as np
import pandas as pd
import folium
import math
import base64
from pyomo.environ import (ConcreteModel, 
                           Var, 
                           ConstraintList, 
                           Objective, 
                           Binary,
                           Reals,
                           PositiveIntegers,
                           SolverFactory)

# initialize solver
solver = SolverFactory("cbc", executable='/usr/bin/cbc')
solver_glpk = solver = SolverFactory('glpk')

In [3]:
cities_data = pd.read_csv("/content/cities_data.csv", index_col=0)
cities_data.head()

id            name        lat        lon  \
0  1640184983          Colaba  18.915091  72.825969   
1    42942995      Mumbai GPO  18.938908  72.836794   
2   620427148       Kalbadevi  18.949258  72.827938   
3  2630075008  Mumbai Central  18.969586  72.819315   
4  4260270146       Tulsiwadi  18.972590  72.815774   

                                            location  
0  Colaba, A Ward, Zone 1, Mumbai, Mumbai City, M...  
1  Mumbai GPO, Walchand Hirachand Road (Fort Stre...  
2  Kalbadevi, C Ward, Zone 1, Mumbai, Mumbai City...  
3  Mumbai Central, J Boman Behram Marg, Cowasji J...  
4  Treebo Trend Rosewood, Tulsiwadi, Hatutma Sita...

In [4]:
cities_distances = pd.read_csv("cities_distances.csv", index_col=0)
cities_distances.head()

Colaba  General post office  Kalba Devi  \
Colaba                    0.0                  4.7         6.5   
General post office       4.7                  0.0         2.2   
Kalba Devi                6.5                  2.2         0.0   
Mumbai Central       100000.0                  5.3    100000.0   
Tulsiwadi            100000.0             100000.0         5.3   

                     Mumbai Central  Tulsiwadi  Worli Naka  Worli police camp  \
Colaba                     100000.0   100000.0    100000.0           100000.0   
General post office             5.3   100000.0    100000.0           100000.0   
Kalba Devi                 100000.0        5.3    100000.0           100000.0   
Mumbai Central                  0.0        3.2         4.5                7.3   
Tulsiwadi                       3.2        0.0         3.8           100000.0   

                        Dadar    Wadala  Anushakti Nagar  ...  Azad Nagar  \
Colaba               100000.0  100000.0         100000.0  ...    100000.0   
General post office       9.7  100000.0         100000.0  ...    100000.0   
Kalba Devi           100000.0  100000.0         100000.0  ...    100000.0   
Mumbai Central            8.5  100000.0         100000.0  ...    100000.0   
Tulsiwadi            100000.0  100000.0         100000.0  ...    100000.0   

                        Seepz  Nahur East   Bhandup  Goregoan    Mulund  \
Colaba               100000.0    100000.0  100000.0  100000.0  100000.0   
General post office  100000.0    100000.0  100000.0  100000.0  100000.0   
Kalba Devi           100000.0    100000.0  100000.0  100000.0  100000.0   
Mumbai Central       100000.0    100000.0  100000.0  100000.0  100000.0   
Tulsiwadi            100000.0    100000.0  100000.0  100000.0  100000.0   

                        Malad   Kharodi  Kandivali  Borivali  
Colaba               100000.0  100000.0   100000.0  100000.0  
General post office  100000.0  100000.0   100000.0  100000.0  
Kalba Devi           100000.0  100000.0   100000.0  100000.0  
Mumbai Central       100000.0  100000.0   100000.0  100000.0  
Tulsiwadi            100000.0  100000.0   100000.0  100000.0  

[5 rows x 34 columns]

In [5]:
cities_demands = pd.read_csv("cities_demands.csv", index_col=0)
cities_demands.head()

id            name  demand
0  1640184983          Colaba       0
1    42942995      Mumbai GPO    -200
2   620427148       Kalbadevi     400
3  2630075008  Mumbai Central    -200
4  4260270146       Tulsiwadi    -100

In [6]:
def get_map(cities_data, cities_distances, cities_demand=None, polylines=None, distances=None):
    cities_coords = cities_data.iloc[:, 2:4].to_numpy()
    cities_names = cities_data.iloc[:, 1].to_numpy()
    cities_dists = cities_distances.to_numpy()
    if cities_demand is not None:
        cities_demand = cities_demand.iloc[:, 2].to_numpy()

    min_pt = (cities_data[['lat', 'lon']].min().values).tolist()
    max_pt = (cities_data[['lat', 'lon']].max().values).tolist()
    
    mymap = folium.Map(location=[18.9690, 72.8777])
    if cities_demand is not None:
        for name, pt, demand in zip(cities_names, cities_coords, cities_demand):
            if demand == 0:
                folium.Marker(list(pt), popup = f'{name} \n {demand}', icon=folium.Icon(color="black", icon="square-parking", prefix="fa")).add_to(mymap)
            elif demand < 0:
                folium.Marker(list(pt), popup = f'{name} \n {demand}', icon=folium.Icon(color="red", icon="truck-pickup", prefix="fa")).add_to(mymap)
            else:
                folium.Marker(list(pt), popup = f'{name} \n {demand}', icon=folium.Icon(color="green", icon="truck-pickup", prefix="fa")).add_to(mymap)
    else:
        for name, pt in zip(cities_names, cities_coords):
            folium.Marker(list(pt), popup = name).add_to(mymap)

    mymap.fit_bounds([min_pt, max_pt])
    if polylines is not None:
        for i in range(len(polylines)):
            line = polylines[i]
            # Calculate the bearing between the two points
            start_point = line[0]
            end_point = line[-1]
            lat1, lon1 = start_point
            lat2, lon2 = end_point
            y = math.sin(lon2-lon1) * math.cos(lat2)
            x = math.cos(lat1)*math.sin(lat2) - math.sin(lat1)*math.cos(lat2)*math.cos(lon2-lon1)
            bearing = math.atan2(y, x) * 180 / math.pi
            # Calculate the midpoint of the polyline
            midpoint = [(line[0][0] + line[1][0]) / 2, (line[0][1] + line[1][1]) / 2]
            if distances is not None:
                folium.PolyLine(line, tooltip=distances[i], popup=distances[i], weight=6, color="#111").add_to(mymap)
            else:
                folium.PolyLine(line, weight=1, color="#111").add_to(mymap)

            # Add an arrow marker to the end of the polyline with the correct rotation
            folium.RegularPolygonMarker(
                location=midpoint,
                color="#111",
                fill_color="#111",
                number_of_sides=3,
                opacity=1,
                radius=10,
                rotation=bearing-90,
                tooltip=''
            ).add_to(mymap)
    return mymap

In [7]:
mymap = get_map(cities_data, cities_distances, cities_demands)
mymap

In [8]:
cities_coords = cities_data.iloc[:, 2:4].values
cities_names = cities_data.iloc[:, 1].values
demand_list = cities_demands.iloc[:, 2].values
distance_matrix = cities_distances.to_numpy()
truck_capacity = 600
print("shape of distance matrix: ", distance_matrix.shape)

shape of distance matrix:  (34, 34)


In [9]:
def PDTSP1Model(distance_matrix, demand_list, vehicle_capacity, depot_index):
    n = len(distance_matrix)
    demand_list[depot_index] = -sum(demand_list)

    model = ConcreteModel(name="1-PDTSP")

    model.x = Var(range(n), range(n), initialize=0.0, domain=Binary)
    model.f = Var(range(n), range(n), initialize=np.inf, domain=Reals)
    model.u = Var(range(n), domain=PositiveIntegers)

    model.objective = Objective(expr=sum(distance_matrix[i, j]*model.x[i, j] for i in range(n) for j in range(n)))

    model.constraints = ConstraintList()
    for i in range(n):
        model.constraints.add(sum(model.x[i, k] for k in range(n) if i != k) == 1)

    for j in range(n):
        model.constraints.add(sum(model.x[k, j] for k in range(n) if j != k) == 1)

    model.constraints.add(model.u[0] == 1)
    for i in range(1, n):
        model.u[i].setlb(2)
        model.u[i].setub(n)

    for i in range(n):
        for j in range(n):
            if i != 0 and j != 0:
                model.constraints.add(model.u[i] - model.u[j] + 1 <= (n-1)*(1-model.x[i, j]))

    for i in range(n):
        model.constraints.add(sum(
            model.f[i, k] for k in range(n) if i != k) - sum(
                model.f[k, i] for k in range(n) if i != k) == demand_list[i])

    for i in range(n):
        for j in range(n):
            model.constraints.add(model.f[i, j] >= 0)
            model.constraints.add(model.f[i, j] <= vehicle_capacity*model.x[i, j])
    return model

In [10]:
model = PDTSP1Model(distance_matrix, demand_list, truck_capacity, depot_index=0)
model.pprint()

Streaming output truncated to the last 5000 lines.
        (25, 15) :  None :   inf :  None : False : False :  Reals
        (25, 16) :  None :   inf :  None : False : False :  Reals
        (25, 17) :  None :   inf :  None : False : False :  Reals
        (25, 18) :  None :   inf :  None : False : False :  Reals
        (25, 19) :  None :   inf :  None : False : False :  Reals
        (25, 20) :  None :   inf :  None : False : False :  Reals
        (25, 21) :  None :   inf :  None : False : False :  Reals
        (25, 22) :  None :   inf :  None : False : False :  Reals
        (25, 23) :  None :   inf :  None : False : False :  Reals
        (25, 24) :  None :   inf :  None : False : False :  Reals
        (25, 25) :  None :   inf :  None : False : False :  Reals
        (25, 26) :  None :   inf :  None : False : False :  Reals
        (25, 27) :  None :   inf :  None : False : False :  Reals
        (25, 28) :  None :   inf :  None : False : False :  Reals
        (25, 29) :  None 

In [11]:
print("Problem Details")
print("."*100)
print("Number of Cities: ", len(distance_matrix))
print("Number of Delivery Points: ", len(demand_list[np.where(demand_list < 0)]))
print("Number of Pickup Points: ", len(demand_list[np.where(demand_list > 0)]))
print("="*100)
print("Model Details: ")
print("."*100)
print("Total Number of variables: ", len(model.x) + len(model.u) + len(model.f))
print("Total Number of constraints: ", len(model.constraints) + 2*len(model.u) + len(model.x) )

Problem Details
....................................................................................................
Number of Cities:  34
Number of Delivery Points:  17
Number of Pickup Points:  16
Model Details: 
....................................................................................................
Total Number of variables:  2346
Total Number of constraints:  4728


In [12]:
%%time
## CBC Solver
result = solver.solve(model)
print("Solver Status: ", result.solver.status)
print("Solver Termination Condition: ", result.solver.termination_condition)

Solver Status:  ok
Solver Termination Condition:  optimal
CPU times: user 972 ms, sys: 96.4 ms, total: 1.07 s
Wall time: 1min 40s


In [13]:
result

{'Problem': [{'Name': 'unknown', 'Lower bound': 197.1, 'Upper bound': 197.1, 'Number of objectives': 1, 'Number of constraints': 3505, 'Number of variables': 2347, 'Number of nonzeros': 11159, 'Sense': 'minimize'}], 'Solver': [{'Status': 'ok', 'Termination condition': 'optimal', 'Statistics': {'Branch and bound': {'Number of bounded subproblems': '8889', 'Number of created subproblems': '8889'}}, 'Error rc': 0, 'Time': 100.44751238822937}], 'Solution': [OrderedDict([('number of solutions', 0), ('number of solutions displayed', 0)])]}

In [14]:
print("optimal objective value: ", model.objective())

optimal objective value:  197.09999999999997


In [15]:
sol_edges = []
for i in range(len(distance_matrix)):
    for j in range(len(distance_matrix)):
        if model.x[i, j].value:
            sol_edges.append((j, i))

In [16]:
polylines = []
for edge in sol_edges:
    inp, out = edge
    inp_coordinate = cities_coords[inp]
    out_coordinate = cities_coords[out]
    polylines.append((inp_coordinate, out_coordinate))

In [17]:
sol_dict = {key:val for key, val in sol_edges}
optimal_path_idx = []
c = 0
idx = 0
while c < len(distance_matrix):
    optimal_path_idx.append(idx)
    idx = sol_dict[idx]
    c += 1
optimal_path_idx.append(0)

In [18]:
optimal_path = [cities_names[i] for i in optimal_path_idx]
for city in optimal_path:
    print(city, " -> ", end="")

Colaba  -> Kalbadevi  -> Tulsiwadi  -> Mumbai Central  -> Worli Naka  -> Worli Police Camp  -> Wadala  -> Bandra West  -> Khar West Mumbai  -> Air India Colony Mumbai  -> Vile Parle East Mumbai  -> MIDC Mumbai  -> Azad Nagar Mumbai  -> Goregaon Mumbai  -> Malad West Mumbai  -> Kandivali Mumbai  -> Borivali Mumbai  -> Kharodi Mumbai  -> Andheri West  -> Jogeshwari East Mumbai  -> Seepz Mumbai  -> Nahur East  -> Mulund  -> Bhandup  -> Powai  -> Andheri Mumbai  -> P&T Colony Mumbai  -> India Post Office Mumbai  -> Kurla West  -> Tilak Nagar Chembur  -> Chembur  -> Anushakti Nagar  -> Dadar  -> Mumbai GPO  -> Colaba  -> 

In [19]:
distances = []
for i in range(len(optimal_path_idx)-1):
    distances.append(f"{distance_matrix[optimal_path_idx[i], optimal_path_idx[i+1]] :.2f} K.M.")

In [20]:
mymap = get_map(cities_data, cities_distances, cities_demands, polylines, distances)
mymap.save("map.html")
mymap

In [21]:
%%time
## GLPK Solver
result = solver_glpk.solve(model)
print("Solver Status: ", result.solver.status)
print("Solver Termination Condition: ", result.solver.termination_condition)

Solver Status:  ok
Solver Termination Condition:  optimal
CPU times: user 719 ms, sys: 82.4 ms, total: 802 ms
Wall time: 1min 35s


In [22]:
result

{'Problem': [{'Name': 'unknown', 'Lower bound': 197.1, 'Upper bound': 197.1, 'Number of objectives': 1, 'Number of constraints': 3505, 'Number of variables': 2347, 'Number of nonzeros': 11159, 'Sense': 'minimize'}], 'Solver': [{'Status': 'ok', 'Termination condition': 'optimal', 'Statistics': {'Branch and bound': {'Number of bounded subproblems': '8889', 'Number of created subproblems': '8889'}}, 'Error rc': 0, 'Time': 94.8987364768982}], 'Solution': [OrderedDict([('number of solutions', 0), ('number of solutions displayed', 0)])]}

In [23]:
print("optimal objective value: ", model.objective())

optimal objective value:  197.09999999999997


In [24]:
sol_edges = []
for i in range(len(distance_matrix)):
    for j in range(len(distance_matrix)):
        if model.x[i, j].value:
            sol_edges.append((j, i))

In [25]:
polylines = []
for edge in sol_edges:
    inp, out = edge
    inp_coordinate = cities_coords[inp]
    out_coordinate = cities_coords[out]
    polylines.append((inp_coordinate, out_coordinate))

In [26]:
sol_dict = {key:val for key, val in sol_edges}
optimal_path_idx = []
c = 0
idx = 0
while c < len(distance_matrix):
    optimal_path_idx.append(idx)
    idx = sol_dict[idx]
    c += 1
optimal_path_idx.append(0)

In [27]:
optimal_path = [cities_names[i] for i in optimal_path_idx]
for city in optimal_path:
    print(city, " -> ", end="")

Colaba  -> Kalbadevi  -> Tulsiwadi  -> Mumbai Central  -> Worli Naka  -> Worli Police Camp  -> Wadala  -> Bandra West  -> Khar West Mumbai  -> Air India Colony Mumbai  -> Vile Parle East Mumbai  -> MIDC Mumbai  -> Azad Nagar Mumbai  -> Goregaon Mumbai  -> Malad West Mumbai  -> Kandivali Mumbai  -> Borivali Mumbai  -> Kharodi Mumbai  -> Andheri West  -> Jogeshwari East Mumbai  -> Seepz Mumbai  -> Nahur East  -> Mulund  -> Bhandup  -> Powai  -> Andheri Mumbai  -> P&T Colony Mumbai  -> India Post Office Mumbai  -> Kurla West  -> Tilak Nagar Chembur  -> Chembur  -> Anushakti Nagar  -> Dadar  -> Mumbai GPO  -> Colaba  -> 

In [28]:
distances = []
for i in range(len(optimal_path_idx)-1):
    distances.append(f"{distance_matrix[optimal_path_idx[i], optimal_path_idx[i+1]] :.2f} K.M.")

In [29]:
mymap = get_map(cities_data, cities_distances, cities_demands, polylines, distances)
mymap

## New Demand 1

In [30]:
cities_demands = pd.read_csv("cities_demands_2.csv", index_col=0)
demand_list = cities_demands.iloc[:, 2].values
cities_demands.head()

id            name  demand
0  1640184983          Colaba       0
1    42942995      Mumbai GPO    -200
2   620427148       Kalbadevi     400
3  2630075008  Mumbai Central    -200
4  4260270146       Tulsiwadi    -100

In [31]:
model = PDTSP1Model(distance_matrix, demand_list, truck_capacity, depot_index=0)
model.pprint()

Streaming output truncated to the last 5000 lines.
        (25, 15) :  None :   inf :  None : False : False :  Reals
        (25, 16) :  None :   inf :  None : False : False :  Reals
        (25, 17) :  None :   inf :  None : False : False :  Reals
        (25, 18) :  None :   inf :  None : False : False :  Reals
        (25, 19) :  None :   inf :  None : False : False :  Reals
        (25, 20) :  None :   inf :  None : False : False :  Reals
        (25, 21) :  None :   inf :  None : False : False :  Reals
        (25, 22) :  None :   inf :  None : False : False :  Reals
        (25, 23) :  None :   inf :  None : False : False :  Reals
        (25, 24) :  None :   inf :  None : False : False :  Reals
        (25, 25) :  None :   inf :  None : False : False :  Reals
        (25, 26) :  None :   inf :  None : False : False :  Reals
        (25, 27) :  None :   inf :  None : False : False :  Reals
        (25, 28) :  None :   inf :  None : False : False :  Reals
        (25, 29) :  None 

In [32]:
print("Problem Details")
print("."*100)
print("Number of Cities: ", len(distance_matrix))
print("Number of Delivery Points: ", len(demand_list[np.where(demand_list < 0)]))
print("Number of Pickup Points: ", len(demand_list[np.where(demand_list > 0)]))
print("="*100)
print("Model Details: ")
print("."*100)
print("Total Number of variables: ", len(model.x) + len(model.u) + len(model.f))
print("Total Number of constraints: ", len(model.constraints) + 2*len(model.u) + len(model.x) )

Problem Details
....................................................................................................
Number of Cities:  34
Number of Delivery Points:  17
Number of Pickup Points:  16
Model Details: 
....................................................................................................
Total Number of variables:  2346
Total Number of constraints:  4728


In [33]:
%%time
## CBC Solver
result = solver.solve(model)
print("Solver Status: ", result.solver.status)
print("Solver Termination Condition: ", result.solver.termination_condition)

Solver Status:  ok
Solver Termination Condition:  optimal
CPU times: user 632 ms, sys: 31.5 ms, total: 663 ms
Wall time: 34.5 s


In [34]:
print("optimal objective value: ", model.objective())

optimal objective value:  201.49999999999994


In [35]:
sol_edges = []
for i in range(len(distance_matrix)):
    for j in range(len(distance_matrix)):
        if model.x[i, j].value:
            sol_edges.append((j, i))

In [36]:
polylines = []
for edge in sol_edges:
    inp, out = edge
    inp_coordinate = cities_coords[inp]
    out_coordinate = cities_coords[out]
    polylines.append((inp_coordinate, out_coordinate))

In [37]:
sol_dict = {key:val for key, val in sol_edges}
optimal_path_idx = []
c = 0
idx = 0
while c < len(distance_matrix):
    optimal_path_idx.append(idx)
    idx = sol_dict[idx]
    c += 1
optimal_path_idx.append(0)

In [38]:
optimal_path = [cities_names[i] for i in optimal_path_idx]
for city in optimal_path:
    print(city, " -> ", end="")

Colaba  -> Kalbadevi  -> Tulsiwadi  -> Mumbai Central  -> Worli Naka  -> Worli Police Camp  -> Wadala  -> Bandra West  -> Air India Colony Mumbai  -> Khar West Mumbai  -> India Post Office Mumbai  -> Vile Parle East Mumbai  -> MIDC Mumbai  -> Azad Nagar Mumbai  -> Goregaon Mumbai  -> Malad West Mumbai  -> Kandivali Mumbai  -> Borivali Mumbai  -> Kharodi Mumbai  -> Andheri West  -> Jogeshwari East Mumbai  -> Seepz Mumbai  -> Nahur East  -> Mulund  -> Bhandup  -> Powai  -> Andheri Mumbai  -> P&T Colony Mumbai  -> Kurla West  -> Tilak Nagar Chembur  -> Chembur  -> Anushakti Nagar  -> Dadar  -> Mumbai GPO  -> Colaba  -> 

In [39]:
distances = []
for i in range(len(optimal_path_idx)-1):
    distances.append(f"{distance_matrix[optimal_path_idx[i], optimal_path_idx[i+1]] :.2f} K.M.")

In [40]:
mymap = get_map(cities_data, cities_distances, cities_demands, polylines, distances)
mymap.save("map1.html")
mymap

## New Demand 2

In [41]:
cities_demands = pd.read_csv("cities_demands_2.csv", index_col=0)
demand_list = cities_demands.iloc[:, 2].values
cities_demands.head()

id            name  demand
0  1640184983          Colaba       0
1    42942995      Mumbai GPO    -200
2   620427148       Kalbadevi     400
3  2630075008  Mumbai Central    -200
4  4260270146       Tulsiwadi    -100

In [42]:
model = PDTSP1Model(distance_matrix, demand_list, truck_capacity, depot_index=0)
model.pprint()

Streaming output truncated to the last 5000 lines.
        (25, 15) :  None :   inf :  None : False : False :  Reals
        (25, 16) :  None :   inf :  None : False : False :  Reals
        (25, 17) :  None :   inf :  None : False : False :  Reals
        (25, 18) :  None :   inf :  None : False : False :  Reals
        (25, 19) :  None :   inf :  None : False : False :  Reals
        (25, 20) :  None :   inf :  None : False : False :  Reals
        (25, 21) :  None :   inf :  None : False : False :  Reals
        (25, 22) :  None :   inf :  None : False : False :  Reals
        (25, 23) :  None :   inf :  None : False : False :  Reals
        (25, 24) :  None :   inf :  None : False : False :  Reals
        (25, 25) :  None :   inf :  None : False : False :  Reals
        (25, 26) :  None :   inf :  None : False : False :  Reals
        (25, 27) :  None :   inf :  None : False : False :  Reals
        (25, 28) :  None :   inf :  None : False : False :  Reals
        (25, 29) :  None 

In [43]:
print("Problem Details")
print("."*100)
print("Number of Cities: ", len(distance_matrix))
print("Number of Delivery Points: ", len(demand_list[np.where(demand_list < 0)]))
print("Number of Pickup Points: ", len(demand_list[np.where(demand_list > 0)]))
print("="*100)
print("Model Details: ")
print("."*100)
print("Total Number of variables: ", len(model.x) + len(model.u) + len(model.f))
print("Total Number of constraints: ", len(model.constraints) + 2*len(model.u) + len(model.x) )

Problem Details
....................................................................................................
Number of Cities:  34
Number of Delivery Points:  17
Number of Pickup Points:  16
Model Details: 
....................................................................................................
Total Number of variables:  2346
Total Number of constraints:  4728


In [44]:
%%time
## CBC Solver
result = solver.solve(model)
print("Solver Status: ", result.solver.status)
print("Solver Termination Condition: ", result.solver.termination_condition)

Solver Status:  ok
Solver Termination Condition:  optimal
CPU times: user 601 ms, sys: 56.2 ms, total: 657 ms
Wall time: 35.5 s


In [45]:
print("optimal objective value: ", model.objective())

optimal objective value:  201.49999999999994


In [46]:
sol_edges = []
for i in range(len(distance_matrix)):
    for j in range(len(distance_matrix)):
        if model.x[i, j].value:
            sol_edges.append((j, i))

In [47]:
polylines = []
for edge in sol_edges:
    inp, out = edge
    inp_coordinate = cities_coords[inp]
    out_coordinate = cities_coords[out]
    polylines.append((inp_coordinate, out_coordinate))

In [48]:
sol_dict = {key:val for key, val in sol_edges}
optimal_path_idx = []
c = 0
idx = 0
while c < len(distance_matrix):
    optimal_path_idx.append(idx)
    idx = sol_dict[idx]
    c += 1
optimal_path_idx.append(0)

In [49]:
optimal_path = [cities_names[i] for i in optimal_path_idx]
for city in optimal_path:
    print(city, " -> ", end="")

Colaba  -> Kalbadevi  -> Tulsiwadi  -> Mumbai Central  -> Worli Naka  -> Worli Police Camp  -> Wadala  -> Bandra West  -> Air India Colony Mumbai  -> Khar West Mumbai  -> India Post Office Mumbai  -> Vile Parle East Mumbai  -> MIDC Mumbai  -> Azad Nagar Mumbai  -> Goregaon Mumbai  -> Malad West Mumbai  -> Kandivali Mumbai  -> Borivali Mumbai  -> Kharodi Mumbai  -> Andheri West  -> Jogeshwari East Mumbai  -> Seepz Mumbai  -> Nahur East  -> Mulund  -> Bhandup  -> Powai  -> Andheri Mumbai  -> P&T Colony Mumbai  -> Kurla West  -> Tilak Nagar Chembur  -> Chembur  -> Anushakti Nagar  -> Dadar  -> Mumbai GPO  -> Colaba  -> 

In [50]:
distances = []
for i in range(len(optimal_path_idx)-1):
    distances.append(f"{distance_matrix[optimal_path_idx[i], optimal_path_idx[i+1]] :.2f} K.M.")

In [51]:
mymap = get_map(cities_data, cities_distances, cities_demands, polylines, distances)
mymap.save("map2.html")
mymap